# Hyper parameter search for CQL

In [1]:
!pip install d3rlpy

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import itertools
import math
import subprocess
import os
import d3rlpy
# plt.style.use('matplotlibrc')

# from Python.data_sampler import *

## Building an MDPDataset

We first read in a large batch of samples from the file. As `d3rlpy` wants it in the form (observations, actions, rewards, terminal flags), we go ahead and do that. Here's a helper function to get a dataset from a list of chunks of your choosing.

In [3]:
import numpy as np
import torch
import random
import pandas
from Python.data_sampler import *

In [4]:
def get_dataset(chunks : list, batch_size=30000, 
                path="collected_data/rl_det_small.txt") -> d3rlpy.dataset.MDPDataset :
    random.seed(0)
    samples = DataSampler(path_to_data=path)
    samples.setting("coarse")
    states = []
    actions = []
    rewards = []
    next_states = []
    for chunk in chunks:
        samples.use_chunk(chunk)
        samples.read_chunk()
        [statesChunk, actionsChunk, rewardsChunk, nextStatesChunk] = samples.get_batch(batch_size)
        states.append(statesChunk)
        actions.append(actionsChunk)
        rewards.append(rewardsChunk)
        next_states.append(nextStatesChunk)
    states = torch.cat(states)
    actions = torch.cat(actions)
    rewards = torch.cat(rewards)
    next_states = torch.cat(next_states)
    terminals = np.zeros(len(states))
    terminals[::1111] = 1 #episode length 100, change if necessary
    print(states.shape)
    dataset = d3rlpy.dataset.MDPDataset(states.numpy(), 
                                        actions.numpy(), 
                                        rewards.numpy(), terminals)
    return dataset, states.numpy(), actions.numpy(), rewards.numpy()

We can build the dataset from there, just like this, and split into train and test sets.

In [5]:
dataset, states, actions, rewards = get_dataset([i+200 for  i in range(100)], path="../collected_data/rl_purestochastic.txt")

start
[ 0.00000000e+00  7.95731469e+08  1.43210892e-01 -3.25999953e-02
 -1.38000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -5.28049971e-01  6.00000000e-01  4.67532035e-01]
Read chunk # 201 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.87189108e-01  2.46000047e-02
 -8.00013420e-04  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01 -5.61927906e-02  2.08952959e-01]
Read chunk # 202 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -1.53789108e-01  1.32000047e-02
  8.79998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -9.71586383e-02 -6.00000000e-01 -5.33093061e-02]
Read chunk # 203 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.39489108e-01 -4.75999953e-02
 -9.30001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01  1.41298638e-01  5.43892365e-01]
Read chunk # 204 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  3.48410892e-01  5.24000047e-02
  2.50999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.

[ 0.00000000e+00  7.95731469e+08  6.16108923e-02 -5.77999953e-02
  2.50999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  1.10771801e-01  4.84326755e-01  6.00000000e-01]
Read chunk # 253 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  7.75108923e-02 -4.85999953e-02
  2.30999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01  3.99697124e-01  2.35547484e-01]
Read chunk # 254 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -1.72989108e-01 -1.95999953e-02
  2.61999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -6.00000000e-01  6.00000000e-01  6.00000000e-01]
Read chunk # 255 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -8.32891077e-02  2.78000047e-02
  1.94999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  3.42318134e-01 -3.84065197e-02  6.00000000e-01]
Read chunk # 256 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -8.29891077e-02  3.62000047e-02
 -1.31000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -6.000000

In [6]:
print("The behavior policy value statistics are:")
dataset.compute_stats()['return']

The behavior policy value statistics are:


{'mean': -269.3442,
 'std': 168.58556,
 'min': -635.52454,
 'max': 0.0,
 'histogram': (array([ 5,  3,  3,  3,  4,  2,  4,  1,  0,  2,  9,  7, 10,  7,  8,  7, 13,
         10,  1,  1]),
  array([-635.52454 , -603.7483  , -571.9721  , -540.19586 , -508.41962 ,
         -476.6434  , -444.8672  , -413.09094 , -381.31473 , -349.53848 ,
         -317.76227 , -285.98605 , -254.20981 , -222.4336  , -190.65736 ,
         -158.88113 , -127.104904,  -95.32868 ,  -63.552452,  -31.776226,
            0.      ], dtype=float32))}

In [7]:
from sklearn.model_selection import train_test_split
train_episodes, test_episodes = train_test_split(dataset, test_size=0.2)

## Setting up an Algorithm

In [8]:
from d3rlpy.algos import CQL
from d3rlpy.models.encoders import VectorEncoderFactory

from d3rlpy.preprocessing import MinMaxActionScaler
import random
action_scaler = MinMaxActionScaler(minimum=-0.6, maximum=0.6)

from d3rlpy.metrics.scorer import td_error_scorer
from d3rlpy.metrics.scorer import average_value_estimation_scorer
from d3rlpy.metrics.scorer import initial_state_value_estimation_scorer

from d3rlpy.ope import FQE
# metrics to evaluate with
from d3rlpy.metrics.scorer import soft_opc_scorer
import pickle as pkl
from statistics import harmonic_mean as hm

## Perform a random search on hyper params. 

As good fqe on both stochastic and deterministic data is needed for good performance during the evaluation step in the simulator, we take the harmonic mean of both fqes to understand the performance on each dataset. The harmonic mean is large only when each number whose mean is being taken is large. Therefore, a large harmonic mean corresponds to large numbers whose mean is being taken.


In [9]:

# The number of times we would wanna do a random search for hyper-params. In 
# every random search, we randomly pick a new set of hyper-params.
num_search_iterations = 40
largest_fqe = -np.inf

for i in range(num_search_iterations):

    random.seed()

    actor_lr_this_iter = random.uniform(1e-5, 1e-2)
    critic_lr_this_iter = random.uniform(1e-5, 1e-2)
    temp_lr_this_iter = random.uniform(1e-5, 1e-4)
    n_steps_this_iter = random.choice([1, 3, 5, 7])

    actor_encoder = VectorEncoderFactory(hidden_units=[12, 24, 36, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)
    critic_encoder = VectorEncoderFactory(hidden_units=[12, 24, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)

    print("search iteration: ", i)
    print("using hyper params: ", [actor_lr_this_iter, critic_lr_this_iter, 
                                   temp_lr_this_iter, n_steps_this_iter])

    model = CQL(q_func_factory='qr', #qr -> quantile regression q function, but you don't have to use this
                reward_scaler='standard',
#                 actor_encoder_factory = actor_encoder,
#                 critic_encoder_factory = critic_encoder,
                action_scaler=action_scaler,
                actor_learning_rate=actor_lr_this_iter, 
                critic_learning_rate=critic_lr_this_iter,
                temp_learning_rate=temp_lr_this_iter,
                n_steps=n_steps_this_iter, 
                use_gpu=True) #change it to true if you have one
    model.build_with_dataset(dataset)

    model.fit(train_episodes,
        eval_episodes=test_episodes,
        n_epochs=50, 
        tensorboard_dir='runs',
        scorers={
            'td_error': td_error_scorer,
            'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i+1000 for i  in range(20)], 
                                                                    path="../collected_data/rl_stochpid.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_stoch = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i for i in range(40)], 
                                                                    path="../collected_data/rl_purestochastic.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_det = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    if(hm([history_stoch[-1][1]["ave_value"] + 50, 
           history_det[-1][1]["ave_value"] + 50]) \
                                                          > largest_fqe):
        largest_fqe = hm([history_stoch[-1][1]["ave_value"] + 50, 
                         history_det[-1][1]["ave_value"] + 50])

        # Save the hyper-params
        hyperparams = [actor_lr_this_iter, critic_lr_this_iter, 
                       temp_lr_this_iter, n_steps_this_iter]

        with open("hyperparams_cql.pkl", "wb") as f:
            print("most optimal hyper params for cql at this point: ", hyperparams)
            pkl.dump(hyperparams, f)

        # Save model and policy
        model.save_model("model_hyperparams_cql.pt")
        model.save_policy("policy_hyperparams_cql.pt")


search iteration:  0
using hyper params:  [0.00019761736773947405, 0.005790530288604701, 4.553524150645552e-05, 5]
2022-04-21 21:26.47 [debug    ] RoundIterator is selected.
2022-04-21 21:26.47 [info     ] Directory is created at d3rlpy_logs/CQL_20220421212647
2022-04-21 21:26.47 [debug    ] Fitting action scaler...       action_scaler=min_max
2022-04-21 21:26.47 [debug    ] Fitting reward scaler...       reward_scaler=standard
2022-04-21 21:26.47 [warning  ] Skip building models since they're already built.
2022-04-21 21:26.47 [info     ] Parameters are saved to d3rlpy_logs/CQL_20220421212647/params.json params={'action_scaler': {'type': 'min_max', 'params': {'minimum': array(-0.6), 'maximum': array(0.6)}}, 'actor_encoder_factory': {'type': 'default', 'params': {'activation': 'relu', 'use_batch_norm': False, 'dropout_rate': None}}, 'actor_learning_rate': 0.00019761736773947405, 'actor_optim_factory': {'optim_cls': 'Adam', 'betas': (0.9, 0.999), 'eps': 1e-08, 'weight_decay': 0, 'amsgra

Epoch 1/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-21 21:26.57 [info     ] CQL_20220421212647: epoch=1 step=342 epoch=1 metrics={'time_sample_batch': 0.0002814189732423303, 'time_algorithm_update': 0.025783455162717586, 'temp_loss': 4.983634201406735, 'temp': 0.9922439306102998, 'alpha_loss': -16.580111891205547, 'alpha': 1.0170159580414755, 'critic_loss': 42.72588180519684, 'actor_loss': 7.580138007451219, 'time_step': 0.026122905357539306, 'td_error': 2.5917201660121028, 'init_value': -15.399798393249512, 'ave_value': -14.433544188898964} step=342
2022-04-21 21:26.57 [info     ] Model parameters are saved to d3rlpy_logs/CQL_20220421212647/model_342.pt


Epoch 2/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-21 21:27.05 [info     ] CQL_20220421212647: epoch=2 step=684 epoch=2 metrics={'time_sample_batch': 0.0002929139555546275, 'time_algorithm_update': 0.023687305506209882, 'temp_loss': 4.796718908332244, 'temp': 0.9771051896594422, 'alpha_loss': -15.310582054985893, 'alpha': 1.0511837246125204, 'critic_loss': 38.451427693952596, 'actor_loss': 16.6349584345232, 'time_step': 0.02404167289622346, 'td_error': 10.368500205115785, 'init_value': -27.519927978515625, 'ave_value': -25.775999521178168} step=684
2022-04-21 21:27.05 [info     ] Model parameters are saved to d3rlpy_logs/CQL_20220421212647/model_684.pt


...

2022-04-22 07:06.58 [info     ] FQE_20220422070536: epoch=49 step=16856 epoch=49 metrics={'time_sample_batch': 0.0001355319522147955, 'time_algorithm_update': 0.004438438387804253, 'loss': 0.3101121837728072, 'time_step': 0.004636995321096376, 'init_value': -15.716436386108398, 'ave_value': -25.947956187244472, 'soft_opc': nan} step=16856


2022-04-22 07:06.58 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220422070536/model_16856.pt


Epoch 50/50:   0%|          | 0/344 [00:00<?, ?it/s]

2022-04-22 07:07.00 [info     ] FQE_20220422070536: epoch=50 step=17200 epoch=50 metrics={'time_sample_batch': 0.00013370915900829227, 'time_algorithm_update': 0.004289261130399482, 'loss': 0.30921731202397496, 'time_step': 0.004484471886657005, 'init_value': -16.072649002075195, 'ave_value': -26.20000437033606, 'soft_opc': nan} step=17200


2022-04-22 07:07.00 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220422070536/model_17200.pt


## Reading hyper params from file

In [10]:
with open("hyperparams_cql.pkl", "rb") as f:
    data = pkl.load(f)

print(data)

[0.008015326902538738, 0.00488678244826896, 5.7138426138602196e-05, 7]
